In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [9]:
df = pd.read_csv('/workspaces/Futures-First/BackTest/data/LE Outrights/LE Dec24_1min.csv')
tick_size = 0.025
tick_price = 10
df['Date'] = pd.to_datetime(df['Date'])
df = df.sort_values(by='Date')
df.set_index('Date', inplace=True)
df

Open     High      Low    Close
Date                                                   
2024-06-03 13:30:00  185.000  185.000  184.650  184.750
2024-06-03 13:31:00  184.700  184.725  184.625  184.650
2024-06-03 13:32:00  184.675  184.875  184.675  184.775
2024-06-03 13:33:00  184.775  184.775  184.675  184.725
2024-06-03 13:34:00  184.725  184.725  184.550  184.575
...                      ...      ...      ...      ...
2024-09-17 18:00:00  179.825  179.900  179.800  179.900
2024-09-17 18:01:00  179.900  179.925  179.800  179.800
2024-09-17 18:02:00  179.800  179.850  179.775  179.775
2024-09-17 18:03:00  179.775  179.850  179.775  179.825
2024-09-17 18:04:00  179.825  179.875  179.800  179.875

[19523 rows x 4 columns]

In [10]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

class BollingerBandStrategy:
    def __init__(self, df, window=20, std_dev=1.5, tick_size=0.025, tick_price=10):
        self.df = df.reset_index(drop=True)
        self.df.index.name = 'Serial'
        self.window = window
        self.std_dev = std_dev
        self.tick_size = tick_size
        self.tick_price = tick_price

    def calculate_bollinger_bands(self):
        self.df['SMA'] = self.df['Close'].rolling(window=self.window).mean()
        self.df['STD'] = self.df['Close'].rolling(window=self.window).std()
        self.df['Upper Band'] = self.df['SMA'] + (self.df['STD'] * self.std_dev)
        self.df['Lower Band'] = self.df['SMA'] - (self.df['STD'] * self.std_dev)

    def detect_outside_bands(self):
        self.df['Outside Upper'] = (self.df['Low'] > self.df['Upper Band']) & (self.df['High'] > self.df['Upper Band'])
        self.df['Outside Lower'] = (self.df['Low'] < self.df['Lower Band']) & (self.df['High'] < self.df['Lower Band'])

    def implement_trading_strategy(self):
        self.df['Position'] = 0
        self.df['Entry Price'] = np.nan
        self.df['Exit Price'] = np.nan
        self.df['Stop Loss'] = np.nan
        self.df['Exit Type'] = ''
        
        in_position = False
        position_type = None
        entry_index = None
        stop_loss = None

        for i in range(1, len(self.df)):
            if not in_position:
                if self.df['Outside Upper'].iloc[i-1]:
                    reference_low = self.df['Low'].iloc[i-1]
                    if self.df['Low'].iloc[i] < reference_low:
                        self.df.loc[self.df.index[i], 'Position'] = -1  # Short
                        self.df.loc[self.df.index[i], 'Entry Price'] = reference_low
                        stop_loss = self.df['High'].iloc[i-1]  # Set SL at reference candle high
                        self.df.loc[self.df.index[i], 'Stop Loss'] = stop_loss
                        in_position = True
                        position_type = 'short'
                        entry_index = i
                elif self.df['Outside Lower'].iloc[i-1]:
                    reference_high = self.df['High'].iloc[i-1]
                    if self.df['High'].iloc[i] > reference_high:
                        self.df.loc[self.df.index[i], 'Position'] = 1  # Long
                        self.df.loc[self.df.index[i], 'Entry Price'] = reference_high
                        stop_loss = self.df['Low'].iloc[i-1]  # Set SL at reference candle low
                        self.df.loc[self.df.index[i], 'Stop Loss'] = stop_loss
                        in_position = True
                        position_type = 'long'
                        entry_index = i
            else:
                if position_type == 'short':
                    if self.df['High'].iloc[i] >= stop_loss:
                        self.df.loc[self.df.index[i], 'Position'] = 0
                        self.df.loc[self.df.index[i], 'Exit Price'] = stop_loss
                        self.df.loc[self.df.index[i], 'Exit Type'] = 'Stop Loss'
                        in_position = False
                        position_type = None
                    elif self.df['High'].iloc[i] > self.df['High'].iloc[i-1]:
                        self.df.loc[self.df.index[i], 'Position'] = 0
                        self.df.loc[self.df.index[i], 'Exit Price'] = self.df['Close'].iloc[i-1]
                        self.df.loc[self.df.index[i], 'Exit Type'] = 'Trend Break'
                        in_position = False
                        position_type = None
                elif position_type == 'long':
                    if self.df['Low'].iloc[i] <= stop_loss:
                        self.df.loc[self.df.index[i], 'Position'] = 0
                        self.df.loc[self.df.index[i], 'Exit Price'] = stop_loss
                        self.df.loc[self.df.index[i], 'Exit Type'] = 'Stop Loss'
                        in_position = False
                        position_type = None
                    elif self.df['Low'].iloc[i] < self.df['Low'].iloc[i-1]:
                        self.df.loc[self.df.index[i], 'Position'] = 0
                        self.df.loc[self.df.index[i], 'Exit Price'] = self.df['Close'].iloc[i-1]
                        self.df.loc[self.df.index[i], 'Exit Type'] = 'Trend Break'
                        in_position = False
                        position_type = None

    def calculate_pnl(self):
        self.df['PnL'] = np.nan
        entry_price = None
        position = 0
        
        for i in range(len(self.df)):
            if pd.notnull(self.df['Entry Price'].iloc[i]):
                entry_price = self.df['Entry Price'].iloc[i]
                position = self.df['Position'].iloc[i]
            elif pd.notnull(self.df['Exit Price'].iloc[i]) and entry_price is not None:
                exit_price = self.df['Exit Price'].iloc[i]
                pnl = (exit_price - entry_price) * position
                self.df.loc[self.df.index[i], 'PnL'] = pnl / self.tick_size * self.tick_price
                entry_price = None
                position = 0

    def run_strategy(self):
        self.calculate_bollinger_bands()
        self.detect_outside_bands()
        self.implement_trading_strategy()
        self.calculate_pnl()
        return self.df

    def print_trade_details(self):
        entries = self.df[self.df['Position'] != 0].copy()
        exits = self.df[self.df['Exit Price'].notnull()].copy()
        
        trades = []
        for i, entry in entries.iterrows():
            exit_row = exits.loc[exits.index > i].iloc[0] if not exits.loc[exits.index > i].empty else None
            if exit_row is not None:
                trade = {
                    'Entry Serial': i,
                    'Entry Price': entry['Entry Price'],
                    'Position': 'Long' if entry['Position'] == 1 else 'Short',
                    'Exit Serial': exit_row.name,
                    'Exit Price': exit_row['Exit Price'],
                    'PnL': exit_row['PnL']
                }
                trades.append(trade)

        print("\nIndividual Trade Details:")
        print("-------------------------")
        for i, trade in enumerate(trades, 1):
            print(f"Trade {i}:")
            print(f"Entry Serial: {trade['Entry Serial']}")
            print(f"Entry Price: {trade['Entry Price']:.2f}")
            print(f"Position: {trade['Position']}")
            print(f"Exit Serial: {trade['Exit Serial']}")
            print(f"Exit Price: {trade['Exit Price']:.2f}")
            print(f"PnL: ${trade['PnL']:.2f}")
            print("-------------------------")

        pnl_series = pd.Series([trade['PnL'] for trade in trades])
        print(f"\nTotal PnL: ${pnl_series.sum():.2f}")
        print(f"Number of trades: {len(trades)}")
        print(f"Win rate: {(pnl_series > 0).mean():.2%}")
        print(f"Average PnL per trade: ${pnl_series.mean():.2f}")

    def plot_strategy(self):
        fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                            vertical_spacing=0.03, subplot_titles=('Price and Bollinger Bands', 'PnL'),
                            row_heights=[0.7, 0.3])

        fig.add_trace(go.Candlestick(x=self.df.index,
                                     open=self.df['Open'],
                                     high=self.df['High'],
                                     low=self.df['Low'],
                                     close=self.df['Close'],
                                     name='Price'),
                      row=1, col=1)

        fig.add_trace(go.Scatter(x=self.df.index, y=self.df['Upper Band'], name='Upper Band', line=dict(color='red', width=1)), row=1, col=1)
        fig.add_trace(go.Scatter(x=self.df.index, y=self.df['Lower Band'], name='Lower Band', line=dict(color='green', width=1)), row=1, col=1)

        long_entries = self.df[self.df['Position'] == 1]
        short_entries = self.df[self.df['Position'] == -1]
        exits = self.df[self.df['Exit Price'].notnull()]
        stop_losses = self.df[self.df['Stop Loss'].notnull()]

        fig.add_trace(go.Scatter(x=long_entries.index, y=long_entries['Entry Price'], mode='markers', 
                                 name='Long Entry', marker=dict(color='green', size=10, symbol='triangle-up')), row=1, col=1)
        fig.add_trace(go.Scatter(x=short_entries.index, y=short_entries['Entry Price'], mode='markers', 
                                 name='Short Entry', marker=dict(color='red', size=10, symbol='triangle-down')), row=1, col=1)
        fig.add_trace(go.Scatter(x=exits.index, y=exits['Exit Price'], mode='markers', 
                                 name='Exit', marker=dict(color='black', size=8, symbol='x')), row=1, col=1)
        fig.add_trace(go.Scatter(x=stop_losses.index, y=stop_losses['Stop Loss'], mode='markers',
                                 name='Stop Loss', marker=dict(color='purple', size=8, symbol='square-open')), row=1, col=1)

        fig.add_trace(go.Bar(x=self.df.index, y=self.df['PnL'], name='PnL'), row=2, col=1)

        fig.update_layout(title='Bollinger Band Trading Strategy with Stop-Loss', height=800, width=1200,
                          showlegend=True, xaxis_rangeslider_visible=False)
        
        fig.update_xaxes(title_text="Serial Number", row=2, col=1)
        fig.update_yaxes(title_text="Price", row=1, col=1)
        fig.update_yaxes(title_text="PnL", row=2, col=1)

        fig.show()

# Example usage
# df = pd.read_csv('your_data.csv')  # Load your data here
strategy = BollingerBandStrategy(df)
df_with_strategy = strategy.run_strategy()
strategy.print_trade_details()
strategy.plot_strategy()


Individual Trade Details:
-------------------------
Trade 1:
Entry Serial: 22
Entry Price: 184.53
Position: Long
Exit Serial: 23
Exit Price: 184.53
PnL: $0.00
-------------------------
Trade 2:
Entry Serial: 24
Entry Price: 184.50
Position: Long
Exit Serial: 25
Exit Price: 184.50
PnL: $0.00
-------------------------
Trade 3:
Entry Serial: 27
Entry Price: 184.45
Position: Long
Exit Serial: 28
Exit Price: 184.55
PnL: $40.00
-------------------------
Trade 4:
Entry Serial: 44
Entry Price: 184.35
Position: Long
Exit Serial: 45
Exit Price: 184.35
PnL: $0.00
-------------------------
Trade 5:
Entry Serial: 56
Entry Price: 184.22
Position: Long
Exit Serial: 61
Exit Price: 184.32
PnL: $40.00
-------------------------
Trade 6:
Entry Serial: 80
Entry Price: 184.03
Position: Long
Exit Serial: 81
Exit Price: 184.15
PnL: $50.00
-------------------------
Trade 7:
Entry Serial: 85
Entry Price: 183.93
Position: Long
Exit Serial: 87
Exit Price: 183.85
PnL: $-30.00
-------------------------
Trade 8:
En